# Lab 07:  Decision Trees



#### Part 1

Train and fine tune a decision tree for the moons dataset  
* Use make_moons(n_samples=10000, noise=0.4) to generate a moons dataset
* Use train_test_split() to split the dataset into a training set and a test set.
* Use grid search with cross-validation (with the help of the GridSearchCV
class) to find good hyperparameter values for a DecisionTreeClassifier.
Hint: try various values for max_leaf_nodes.
* Train it on the full training set using these hyperparameters, and measure
your model’s performance on the test set. You should get roughly 85% to 87%
accuracy.

In [3]:
from sklearn.datasets import make_moons
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score


x_moons, y_moons = make_moons(n_samples=1000, noise=0.4)
x_train, x_test, y_train, y_test = train_test_split(x_moons, y_moons, random_state=42)

clf = DecisionTreeClassifier()

x_moons

array([[ 0.47256342,  0.07921758],
       [ 0.66175021,  0.42332146],
       [ 0.78382433,  0.50529152],
       ...,
       [ 0.36436801, -0.42889532],
       [-0.97026684, -0.2069905 ],
       [-0.29092074,  0.99309591]])

In [4]:
param_grid = {
    'max_leaf_nodes': [None, 5, 10, 20, 50, 100],
    'max_depth': [None, 3, 5, 10],
    'min_samples_split': [2, 5, 10]
}

grid_search = GridSearchCV(
    estimator=clf, 
    param_grid=param_grid, 
    cv=5,  # 5-fold cross-validation
    scoring='accuracy', # Use accuracy as the evaluation metric
    n_jobs=-1 # Use all available CPU cores
)

grid_search.fit(x_train, y_train)

# Get the best hyperparameters and model
best_params = grid_search.best_params_
best_model = grid_search.best_estimator_

# evaluate the best model on the test set
y_pred = best_model.predict(x_test)
test_accuracy = accuracy_score(y_test, y_pred)

# Print the results
print("Best hyperparameters:", best_params)
print("Test set accuracy with best model:", test_accuracy)

Best hyperparameters: {'max_depth': None, 'max_leaf_nodes': 5, 'min_samples_split': 2}
Test set accuracy with best model: 0.816


#### Part 2: Grow a forest by following these steps:

* Continuing the previous exercise, generate 1,000 subsets of the training set,
each containing 100 instances selected randomly. Hint: you can use Scikit-
Learn’s ShuffleSplit class for this.
* Train one Decision Tree on each subset, using the best hyperparameter values
found in the previous exercise. Evaluate these 1,000 Decision Trees on the test
set. Since they were trained on smaller sets, these Decision Trees will likely
perform worse than the first Decision Tree, achieving only about 80%
accuracy.
* Now comes the magic. For each test set instance, generate the predictions of
the 1,000 Decision Trees, and keep only the most frequent prediction (you can
use SciPy’s mode() function for this). This approach gives you majority-vote
predictions over the test set.
* Evaluate these predictions on the test set: you should obtain a slightly higher
accuracy than your first model (about 0.5 to 1.5% higher). Congratulations,
you have trained a Random Forest classifier!

In [6]:
from sklearn.model_selection import ShuffleSplit
import numpy as np

n_subsets = 1000
subset_size = 100
shuffle_split = ShuffleSplit(n_splits=n_subsets, train_size=subset_size, random_state=42)

subsets_X = []
subsets_y = []

# generate the subsets
for train_index, _ in shuffle_split.split(x_train):
    X_subset = x_train[train_index]
    y_subset = y_train[train_index]
    subsets_X.append(X_subset)
    subsets_y.append(y_subset)

subsets_X

[array([[ 1.94910923, -0.13043047],
        [ 1.99862452, -0.25672143],
        [ 1.17319218,  0.89601171],
        [ 0.34439573, -0.8110366 ],
        [ 0.2702319 , -0.63057063],
        [-0.13867888, -0.02887073],
        [-0.60596763, -0.16554347],
        [-1.25213615,  0.32538482],
        [ 0.0559668 ,  0.92343249],
        [-0.92910061,  0.02932391],
        [ 1.55125224,  0.29077959],
        [ 0.09805491,  1.23204763],
        [ 0.84705045,  0.27335971],
        [-0.79408032,  0.15662128],
        [-0.33322032,  1.274115  ],
        [ 0.77751629,  0.35199827],
        [ 0.65778835,  0.71397092],
        [-0.93946243, -0.63263239],
        [ 0.66135758,  0.46585009],
        [ 0.75755554, -0.35123579],
        [ 1.05294287, -0.09607441],
        [ 0.43626755, -0.43777987],
        [-0.44629145, -0.04965152],
        [-0.05719601,  0.60991492],
        [-0.37138782,  0.007757  ],
        [ 2.00332397,  0.33311271],
        [ 1.67646846,  0.65182102],
        [-0.1079467 ,  0.413

Train one Decision Tree on each subset, using the best hyperparameter values found in the previous exercise. Evaluate these 1,000 Decision Trees on the test set. Since they were trained on smaller sets, these Decision Trees will likely perform worse than the first Decision Tree, achieving only about 80% accuracy.

In [8]:
accuracies = []
predictions = []

for X_subset, y_subset in zip(subsets_X, subsets_y):
    # X_subset is a 2D array of shape (100, 4)
    # y_subset is a 1D array of shape(100,)
    clf = DecisionTreeClassifier(max_depth=None, max_leaf_nodes=10, min_samples_split=2, random_state=42)
    clf.fit(X_subset, y_subset)
    y_pred = clf.predict(x_test)
    predictions.append(y_pred)
    accuracy = accuracy_score(y_test, y_pred)
    accuracies.append(accuracy)

mean_accuracy = np.mean(accuracies)
print(f'Mean accuracy = {mean_accuracy}')

Mean accuracy = 0.779924


Now comes the magic. For each test set instance, generate the predictions of the 1,000 Decision Trees, and keep only the most frequent prediction (you can use SciPy’s mode() function for this). This approach gives you majority-vote predictions over the test set.

In [10]:
from scipy.stats import mode

all_predictions = np.zeros((x_test.shape[0], n_subsets))

# Train 1,000 Decision Trees and collect their predictions
for i, (X_subset, y_subset) in enumerate(zip(subsets_X, subsets_y)):
    clf = DecisionTreeClassifier(random_state=42)
    clf.fit(X_subset, y_subset)
    y_pred = clf.predict(x_test)
    all_predictions[:, i] = y_pred

# Compute the mode (most frequent prediction) for each test instance
# Each row corresponds to a test instance, 
# and each column corresponds to the prediction from one of the 1,000 trees.
majority_vote_predictions, _ = mode(all_predictions, axis=1)
majority_vote_predictions = majority_vote_predictions.ravel()

# Evaluate the accuracy of the majority-vote predictions
accuracy = accuracy_score(y_test, majority_vote_predictions)
print("Majority-vote accuracy:", accuracy)

Majority-vote accuracy: 0.828


I completed this assignment solo